Import the needed libraries

In [1]:
##Import the libraries needed

import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


1. Start retreiving and cleaning the data

In [2]:
# All Missouri Assesment Program (MAP) data is retrieved from the Missouri Department of Elementrary and Secondary Education (MO DESE)
#Retreive data at this portal https://apps.dese.mo.gov/MCDS/Home.aspx

# Retreive assessment data on all schools from Students > MAP Data > "School -- content area all and disag 2019"
MAP = pd.DataFrame(pd.read_csv('School - State Assessment Results.csv'))
MAP.replace("\*", np.NaN, regex= True, inplace = True)



#Set Unique ID for each school
MAP['UNIQUE_ID'] = MAP['COUNTY_DISTRICT']/MAP['SCHOOL_CODE']

#Retrieve only English scores and save to df
MAP_Eng = MAP[MAP['CONTENT_AREA'] == "Eng. Language Arts"]
pd.DataFrame(MAP_Eng)

#Split Eng scores in seperate race df
MAP_Eng_White = pd.DataFrame(MAP_Eng[MAP_Eng['TYPE'] == "White (not Hispanic)"])
MAP_Eng_White.rename(columns={"BELOW_BASIC_PCT":"ENG_WHITE_BELOW_BASIC_PCT", 
                              "BASIC_PCT":"ENG_WHITE_BASIC_PCT", 
                              "PROFICIENT_PCT":"ENG_WHITE_PROFICIENT_PCT", 
                              "ADVANCED_PCT":"ENG_WHITE_ADVANCED_PCT"}, inplace = True)
MAP_Eng_White[['ENG_WHITE_BELOW_BASIC_PCT',
               'ENG_WHITE_BASIC_PCT', 
               'ENG_WHITE_PROFICIENT_PCT', 
               'ENG_WHITE_ADVANCED_PCT']] = MAP_Eng_White[['ENG_WHITE_BELOW_BASIC_PCT',
                                                           'ENG_WHITE_BASIC_PCT', 
                                                           'ENG_WHITE_PROFICIENT_PCT', 
                                                           'ENG_WHITE_ADVANCED_PCT']].astype(float)

MAP_Eng_API = pd.DataFrame(MAP_Eng[MAP_Eng['TYPE'] == "Asian/Pacific Islander"])
MAP_Eng_API.rename(columns={"BELOW_BASIC_PCT":"ENG_API_BELOW_BASIC_PCT", 
                            "BASIC_PCT":"ENG_API_BASIC_PCT", 
                            "PROFICIENT_PCT":"ENG_API_PROFICIENT_PCT", 
                            "ADVANCED_PCT":"ENG_API_ADVANCED_PCT"}, inplace = True)
MAP_Eng_API[['ENG_API_BELOW_BASIC_PCT',
             'ENG_API_BASIC_PCT', 
             'ENG_API_PROFICIENT_PCT', 
             'ENG_API_ADVANCED_PCT']] = MAP_Eng_API[['ENG_API_BELOW_BASIC_PCT',
                                                     'ENG_API_BASIC_PCT', 
                                                     'ENG_API_PROFICIENT_PCT', 
                                                     'ENG_API_ADVANCED_PCT']].astype(float)

MAP_Eng_Black = pd.DataFrame(MAP_Eng[MAP_Eng['TYPE'] == "Black (not Hispanic)"])
MAP_Eng_Black.rename(columns={"BELOW_BASIC_PCT":"ENG_BLACK_BELOW_BASIC_PCT", 
                              "BASIC_PCT":"ENG_BLACK_BASIC_PCT", 
                              "PROFICIENT_PCT":"ENG_BLACK_PROFICIENT_PCT", 
                              "ADVANCED_PCT":"ENG_BLACK_ADVANCED_PCT"}, inplace = True)
MAP_Eng_Black[['ENG_BLACK_BELOW_BASIC_PCT',
             'ENG_BLACK_BASIC_PCT', 
             'ENG_BLACK_PROFICIENT_PCT', 
             'ENG_BLACK_ADVANCED_PCT']] = MAP_Eng_Black[['ENG_BLACK_BELOW_BASIC_PCT',
                                                     'ENG_BLACK_BASIC_PCT', 
                                                     'ENG_BLACK_PROFICIENT_PCT', 
                                                     'ENG_BLACK_ADVANCED_PCT']].astype(float)

MAP_Eng_Hispanic = pd.DataFrame(MAP_Eng[MAP_Eng['TYPE'] == "Hispanic"])
MAP_Eng_Hispanic.rename(columns={"BELOW_BASIC_PCT":"ENG_HISP_BELOW_BASIC_PCT", 
                                 "BASIC_PCT":"ENG_HISP_BASIC_PCT", 
                                 "PROFICIENT_PCT":"ENG_HISP_PROFICIENT_PCT", 
                                 "ADVANCED_PCT":"ENG_HISP_ADVANCED_PCT"}, inplace = True)
MAP_Eng_Hispanic[['ENG_HISP_BELOW_BASIC_PCT',
             'ENG_HISP_BASIC_PCT', 
             'ENG_HISP_PROFICIENT_PCT', 
             'ENG_HISP_ADVANCED_PCT']] = MAP_Eng_Hispanic[['ENG_HISP_BELOW_BASIC_PCT',
                                                     'ENG_HISP_BASIC_PCT', 
                                                     'ENG_HISP_PROFICIENT_PCT', 
                                                     'ENG_HISP_ADVANCED_PCT']].astype(float)

MAP_Eng_Multi = pd.DataFrame(MAP_Eng[MAP_Eng['TYPE'] == "Multiracial"])
MAP_Eng_Multi.rename(columns={"BELOW_BASIC_PCT":"ENG_MULTI_BELOW_BASIC_PCT", 
                              "BASIC_PCT":"ENG_MULTI_BASIC_PCT", 
                              "PROFICIENT_PCT":"ENG_MULTI_PROFICIENT_PCT", 
                              "ADVANCED_PCT":"ENG_MULTI_ADVANCED_PCT"}, inplace = True)
MAP_Eng_Multi[['ENG_MULTI_BELOW_BASIC_PCT',
             'ENG_MULTI_BASIC_PCT', 
             'ENG_MULTI_PROFICIENT_PCT', 
             'ENG_MULTI_ADVANCED_PCT']] = MAP_Eng_Multi[['ENG_MULTI_BELOW_BASIC_PCT',
                                                     'ENG_MULTI_BASIC_PCT', 
                                                     'ENG_MULTI_PROFICIENT_PCT', 
                                                     'ENG_MULTI_ADVANCED_PCT']].astype(float)

MAP_Eng_Native = pd.DataFrame(MAP_Eng[MAP_Eng['TYPE'] == "Amer. Indian or Alaska Native"])
MAP_Eng_Native.rename(columns={"BELOW_BASIC_PCT":"ENG_NATIVE_BELOW_BASIC_PCT", 
                               "BASIC_PCT":"ENG_NATIVE_BASIC_PCT", 
                               "PROFICIENT_PCT":"ENG_NATIVE_PROFICIENT_PCT", 
                               "ADVANCED_PCT":"ENG_NATIVE_ADVANCED_PCT"}, inplace = True)
MAP_Eng_Native[['ENG_NATIVE_BELOW_BASIC_PCT',
             'ENG_NATIVE_BASIC_PCT', 
             'ENG_NATIVE_PROFICIENT_PCT', 
             'ENG_NATIVE_ADVANCED_PCT']] = MAP_Eng_Native[['ENG_NATIVE_BELOW_BASIC_PCT',
                                                     'ENG_NATIVE_BASIC_PCT', 
                                                     'ENG_NATIVE_PROFICIENT_PCT', 
                                                     'ENG_NATIVE_ADVANCED_PCT']].astype(float)

#Retrieve only Mathematics scores
MAP_Math = MAP[MAP['CONTENT_AREA'] == 'Mathematics']

#Split Math scores by race into different df
MAP_Math_White = pd.DataFrame(MAP_Math[MAP_Math['TYPE'] == "White (not Hispanic)"])
MAP_Math_White.rename(columns={"BELOW_BASIC_PCT":"MATH_WHITE_BELOW_BASIC_PCT", 
                               "BASIC_PCT":"MATH_WHITE_BASIC_PCT", 
                               "PROFICIENT_PCT":"MATH_WHITE_PROFICIENT_PCT", 
                               "ADVANCED_PCT":"MATH_WHITE_ADVANCED_PCT"}, inplace = True)
MAP_Math_White[['MATH_WHITE_BELOW_BASIC_PCT',
               'MATH_WHITE_BASIC_PCT', 
               'MATH_WHITE_PROFICIENT_PCT', 
               'MATH_WHITE_ADVANCED_PCT']] = MAP_Math_White[['MATH_WHITE_BELOW_BASIC_PCT',
                                                           'MATH_WHITE_BASIC_PCT', 
                                                           'MATH_WHITE_PROFICIENT_PCT', 
                                                           'MATH_WHITE_ADVANCED_PCT']].astype(float)

MAP_Math_API = pd.DataFrame(MAP_Math[MAP_Math['TYPE'] == "Asian/Pacific Islander"])
MAP_Math_API.rename(columns={"BELOW_BASIC_PCT":"MATH_API_BELOW_BASIC_PCT", 
                             "BASIC_PCT":"MATH_API_BASIC_PCT", 
                             "PROFICIENT_PCT":"MATH_API_PROFICIENT_PCT", 
                             "ADVANCED_PCT":"MATH_API_ADVANCED_PCT"}, inplace = True)
MAP_Math_API[['MATH_API_BELOW_BASIC_PCT',
               'MATH_API_BASIC_PCT', 
               'MATH_API_PROFICIENT_PCT', 
               'MATH_API_ADVANCED_PCT']] = MAP_Math_API[['MATH_API_BELOW_BASIC_PCT',
                                                           'MATH_API_BASIC_PCT', 
                                                           'MATH_API_PROFICIENT_PCT', 
                                                           'MATH_API_ADVANCED_PCT']].astype(float)

MAP_Math_Black = pd.DataFrame(MAP_Math[MAP_Math['TYPE'] == "Black (not Hispanic)"])
MAP_Math_Black.rename(columns={"BELOW_BASIC_PCT":"MATH_BLACK_BELOW_BASIC_PCT", 
                               "BASIC_PCT":"MATH_BLACK_BASIC_PCT", 
                               "PROFICIENT_PCT":"MATH_BLACK_PROFICIENT_PCT", 
                               "ADVANCED_PCT":"MATH_BLACK_ADVANCED_PCT"}, inplace = True)
MAP_Math_Black[['MATH_BLACK_BELOW_BASIC_PCT',
               'MATH_BLACK_BASIC_PCT', 
               'MATH_BLACK_PROFICIENT_PCT', 
               'MATH_BLACK_ADVANCED_PCT']] = MAP_Math_Black[['MATH_BLACK_BELOW_BASIC_PCT',
                                                           'MATH_BLACK_BASIC_PCT', 
                                                           'MATH_BLACK_PROFICIENT_PCT', 
                                                           'MATH_BLACK_ADVANCED_PCT']].astype(float)

MAP_Math_Hispanic = pd.DataFrame(MAP_Math[MAP_Math['TYPE'] == "Hispanic"])
MAP_Math_Hispanic.rename(columns={"BELOW_BASIC_PCT":"MATH_HISP_BELOW_BASIC_PCT", 
                                  "BASIC_PCT":"MATH_HISP_BASIC_PCT", 
                                  "PROFICIENT_PCT":"MATH_HISP_PROFICIENT_PCT", 
                                  "ADVANCED_PCT":"MATH_HISP_ADVANCED_PCT"}, inplace = True)
MAP_Math_Hispanic[['MATH_HISP_BELOW_BASIC_PCT',
               'MATH_HISP_BASIC_PCT', 
               'MATH_HISP_PROFICIENT_PCT', 
               'MATH_HISP_ADVANCED_PCT']] = MAP_Math_Hispanic[['MATH_HISP_BELOW_BASIC_PCT',
                                                           'MATH_HISP_BASIC_PCT', 
                                                           'MATH_HISP_PROFICIENT_PCT', 
                                                           'MATH_HISP_ADVANCED_PCT']].astype(float)

MAP_Math_Multi = pd.DataFrame(MAP_Math[MAP_Math['TYPE'] == "Multiracial"])
MAP_Math_Multi.rename(columns={"BELOW_BASIC_PCT":"MATH_MULTI_BELOW_BASIC_PCT", 
                               "BASIC_PCT":"MATH_MULTI_BASIC_PCT", 
                               "PROFICIENT_PCT":"MATH_MULTI_PROFICIENT_PCT", 
                               "ADVANCED_PCT":"MATH_MULTI_ADVANCED_PCT"}, inplace = True)
MAP_Math_Multi[['MATH_MULTI_BELOW_BASIC_PCT',
               'MATH_MULTI_BASIC_PCT', 
               'MATH_MULTI_PROFICIENT_PCT', 
               'MATH_MULTI_ADVANCED_PCT']] = MAP_Math_Multi[['MATH_MULTI_BELOW_BASIC_PCT',
                                                           'MATH_MULTI_BASIC_PCT', 
                                                           'MATH_MULTI_PROFICIENT_PCT', 
                                                           'MATH_MULTI_ADVANCED_PCT']].astype(float)

MAP_Math_Native = pd.DataFrame(MAP_Math[MAP_Math['TYPE'] == "Amer. Indian or Alaska Native"])
MAP_Math_Native.rename(columns={"BELOW_BASIC_PCT":"MATH_NATIVE_BELOW_BASIC_PCT", 
                                "BASIC_PCT":"MATH_NATIVE_BASIC_PCT", 
                                "PROFICIENT_PCT":"MATH_NATIVE_PROFICIENT_PCT", 
                                "ADVANCED_PCT":"MATH_NATIVE_ADVANCED_PCT"}, inplace = True)
MAP_Math_Native[['MATH_NATIVE_BELOW_BASIC_PCT',
               'MATH_NATIVE_BASIC_PCT', 
               'MATH_NATIVE_PROFICIENT_PCT', 
               'MATH_NATIVE_ADVANCED_PCT']] = MAP_Math_Native[['MATH_NATIVE_BELOW_BASIC_PCT',
                                                           'MATH_NATIVE_BASIC_PCT', 
                                                           'MATH_NATIVE_PROFICIENT_PCT', 
                                                           'MATH_NATIVE_ADVANCED_PCT']].astype(float)

#Retrieve only Science scores
MAP_Sci = MAP[MAP['CONTENT_AREA'] == "Science"]

#Split science scores by race
MAP_Sci_White = pd.DataFrame(MAP_Sci[MAP_Sci['TYPE'] == "White (not Hispanic)"])
MAP_Sci_White.rename(columns={"BELOW_BASIC_PCT":"SCI_WHITE_BELOW_BASIC_PCT", 
                              "BASIC_PCT":"SCI_WHITE_BASIC_PCT", 
                              "PROFICIENT_PCT":"SCI_WHITE_PROFICIENT_PCT", 
                              "ADVANCED_PCT":"SCI_WHITE_ADVANCED_PCT"}, inplace = True)
MAP_Sci_White[['SCI_WHITE_BELOW_BASIC_PCT',
               'SCI_WHITE_BASIC_PCT', 
               'SCI_WHITE_PROFICIENT_PCT', 
               'SCI_WHITE_ADVANCED_PCT']] = MAP_Sci_White[['SCI_WHITE_BELOW_BASIC_PCT',
                                                           'SCI_WHITE_BASIC_PCT', 
                                                           'SCI_WHITE_PROFICIENT_PCT', 
                                                           'SCI_WHITE_ADVANCED_PCT']].astype(float)

MAP_Sci_API = pd.DataFrame(MAP_Sci[MAP_Sci['TYPE'] == "Asian/Pacific Islander"])
MAP_Sci_API.rename(columns={"BELOW_BASIC_PCT":"SCI_API_BELOW_BASIC_PCT", 
                            "BASIC_PCT":"SCI_API_BASIC_PCT", 
                            "PROFICIENT_PCT":"SCI_API_PROFICIENT_PCT", 
                            "ADVANCED_PCT":"SCI_API_ADVANCED_PCT"}, inplace = True)
MAP_Sci_API[['SCI_API_BELOW_BASIC_PCT',
               'SCI_API_BASIC_PCT', 
               'SCI_API_PROFICIENT_PCT', 
               'SCI_API_ADVANCED_PCT']] = MAP_Sci_API[['SCI_API_BELOW_BASIC_PCT',
                                                           'SCI_API_BASIC_PCT', 
                                                           'SCI_API_PROFICIENT_PCT', 
                                                           'SCI_API_ADVANCED_PCT']].astype(float)

MAP_Sci_Black = pd.DataFrame(MAP_Sci[MAP_Sci['TYPE'] == "Black (not Hispanic)"])
MAP_Sci_Black.rename(columns={"BELOW_BASIC_PCT":"SCI_BLACK_BELOW_BASIC_PCT", 
                              "BASIC_PCT":"SCI_BLACK_BASIC_PCT", 
                              "PROFICIENT_PCT":"SCI_BLACK_PROFICIENT_PCT", 
                              "ADVANCED_PCT":"SCI_BLACK_ADVANCED_PCT"}, inplace = True)
MAP_Sci_Black[['SCI_BLACK_BELOW_BASIC_PCT',
               'SCI_BLACK_BASIC_PCT', 
               'SCI_BLACK_PROFICIENT_PCT', 
               'SCI_BLACK_ADVANCED_PCT']] = MAP_Sci_Black[['SCI_BLACK_BELOW_BASIC_PCT',
                                                           'SCI_BLACK_BASIC_PCT', 
                                                           'SCI_BLACK_PROFICIENT_PCT', 
                                                           'SCI_BLACK_ADVANCED_PCT']].astype(float)

MAP_Sci_Hispanic = pd.DataFrame(MAP_Sci[MAP_Sci['TYPE'] == "Hispanic"])
MAP_Sci_Hispanic.rename(columns={"BELOW_BASIC_PCT":"SCI_HISP_BELOW_BASIC_PCT", 
                                 "BASIC_PCT":"SCI_HISP_BASIC_PCT", 
                                 "PROFICIENT_PCT":"SCI_HISP_PROFICIENT_PCT", 
                                 "ADVANCED_PCT":"SCI_HISP_ADVANCED_PCT"}, inplace = True)
MAP_Sci_Hispanic[['SCI_HISP_BELOW_BASIC_PCT',
               'SCI_HISP_BASIC_PCT', 
               'SCI_HISP_PROFICIENT_PCT', 
               'SCI_HISP_ADVANCED_PCT']] = MAP_Sci_Hispanic[['SCI_HISP_BELOW_BASIC_PCT',
                                                           'SCI_HISP_BASIC_PCT', 
                                                           'SCI_HISP_PROFICIENT_PCT', 
                                                           'SCI_HISP_ADVANCED_PCT']].astype(float)

MAP_Sci_Multi = pd.DataFrame(MAP_Sci[MAP_Sci['TYPE'] == "Multiracial"])
MAP_Sci_Multi.rename(columns={"BELOW_BASIC_PCT":"SCI_MULTI_BELOW_BASIC_PCT", 
                              "BASIC_PCT":"SCI_MULTI_BASIC_PCT", 
                              "PROFICIENT_PCT":"SCI_MULTI_PROFICIENT_PCT", 
                              "ADVANCED_PCT":"SCI_MULTI_ADVANCED_PCT"}, inplace = True)
MAP_Sci_Multi[['SCI_MULTI_BELOW_BASIC_PCT',
               'SCI_MULTI_BASIC_PCT', 
               'SCI_MULTI_PROFICIENT_PCT', 
               'SCI_MULTI_ADVANCED_PCT']] = MAP_Sci_Multi[['SCI_MULTI_BELOW_BASIC_PCT',
                                                           'SCI_MULTI_BASIC_PCT', 
                                                           'SCI_MULTI_PROFICIENT_PCT', 
                                                           'SCI_MULTI_ADVANCED_PCT']].astype(float)

MAP_Sci_Native = pd.DataFrame(MAP_Sci[MAP_Sci['TYPE'] == "Amer. Indian or Alaska Native"])
MAP_Sci_Native.rename(columns={"BELOW_BASIC_PCT":"SCI_NATIVE_BELOW_BASIC_PCT", 
                               "BASIC_PCT":"SCI_NATIVE_BASIC_PCT", 
                               "PROFICIENT_PCT":"SCI_NATIVE_PROFICIENT_PCT", 
                               "ADVANCED_PCT":"SCI_NATIVE_ADVANCED_PCT"}, inplace = True)
MAP_Sci_Native[['SCI_NATIVE_BELOW_BASIC_PCT',
               'SCI_NATIVE_BASIC_PCT', 
               'SCI_NATIVE_PROFICIENT_PCT', 
               'SCI_NATIVE_ADVANCED_PCT']] = MAP_Sci_Native[['SCI_NATIVE_BELOW_BASIC_PCT',
                                                           'SCI_NATIVE_BASIC_PCT', 
                                                           'SCI_NATIVE_PROFICIENT_PCT',
                                                           'SCI_NATIVE_ADVANCED_PCT']].astype(float)
#Merge all racial performance dfs onto one df
merge1 = pd.DataFrame(pd.merge(MAP_Eng_White, MAP_Eng_API, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge2 = pd.DataFrame(pd.merge(merge1, MAP_Eng_Black, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge3 = pd.DataFrame(pd.merge(merge2, MAP_Eng_Hispanic, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge4 = pd.DataFrame(pd.merge(merge3, MAP_Eng_Multi, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge5 = pd.DataFrame(pd.merge(merge4, MAP_Eng_Native, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge6 = pd.DataFrame(pd.merge(merge5, MAP_Math_White, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge7 = pd.DataFrame(pd.merge(merge6, MAP_Math_API, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge8 = pd.DataFrame(pd.merge(merge7, MAP_Math_Black, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge9 = pd.DataFrame(pd.merge(merge8, MAP_Math_Hispanic, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge10 = pd.DataFrame(pd.merge(merge9, MAP_Math_Multi, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge11 = pd.DataFrame(pd.merge(merge10, MAP_Math_Native, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge12 = pd.DataFrame(pd.merge(merge11, MAP_Sci_White, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge13 = pd.DataFrame(pd.merge(merge12, MAP_Sci_API, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge14 = pd.DataFrame(pd.merge(merge13, MAP_Sci_Black, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge15 = pd.DataFrame(pd.merge(merge14, MAP_Sci_Hispanic, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge16 = pd.DataFrame(pd.merge(merge15, MAP_Sci_Multi, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))
merge17 = pd.DataFrame(pd.merge(merge16, MAP_Sci_Native, on=["COUNTY_DISTRICT", "SCHOOL_CODE", "SCHOOL_NAME", "DISTRICT_NAME"], how='outer'))

Full_Merge = pd.DataFrame(merge17)

## Generate a Score Index to describe racial performance disparity among schools.

# Score Index = Percent of white students scoring at perfroamnce level / the avg of all non-white students scoring at performance level
# A Score Index of 1 means that an equal number of white students and non-white students score at the same performance level
# A Score Index less than 1 means that more non-white students score at the perfroamnce level than white students
# A Score Index greater than one means that more white students score a performance level than non-white students

MAP_Scores_Index = pd.DataFrame(Full_Merge[['COUNTY_DISTRICT',
                                           'DISTRICT_NAME',
                                           'SCHOOL_CODE',
                                           'SCHOOL_NAME',
                                           'ENG_WHITE_BELOW_BASIC_PCT',
                                                    'ENG_WHITE_BASIC_PCT', 
                                                    'ENG_WHITE_PROFICIENT_PCT', 
                                                    'ENG_WHITE_ADVANCED_PCT',
                                           'ENG_API_BELOW_BASIC_PCT',
                                                     'ENG_API_BASIC_PCT', 
                                                     'ENG_API_PROFICIENT_PCT', 
                                                     'ENG_API_ADVANCED_PCT',
                                           'ENG_BLACK_BELOW_BASIC_PCT',
                                                     'ENG_BLACK_BASIC_PCT', 
                                                     'ENG_BLACK_PROFICIENT_PCT', 
                                                     'ENG_BLACK_ADVANCED_PCT',
                                           'ENG_HISP_BELOW_BASIC_PCT',
                                                     'ENG_HISP_BASIC_PCT', 
                                                     'ENG_HISP_PROFICIENT_PCT', 
                                                     'ENG_HISP_ADVANCED_PCT',
                                            'ENG_MULTI_BELOW_BASIC_PCT',
                                                     'ENG_MULTI_BASIC_PCT', 
                                                     'ENG_MULTI_PROFICIENT_PCT', 
                                                     'ENG_MULTI_ADVANCED_PCT',
                                            'ENG_NATIVE_BELOW_BASIC_PCT',
                                                     'ENG_NATIVE_BASIC_PCT', 
                                                     'ENG_NATIVE_PROFICIENT_PCT', 
                                                     'ENG_NATIVE_ADVANCED_PCT',
                                           'MATH_WHITE_BELOW_BASIC_PCT',
                                                           'MATH_WHITE_BASIC_PCT', 
                                                           'MATH_WHITE_PROFICIENT_PCT', 
                                                           'MATH_WHITE_ADVANCED_PCT',
                                            'MATH_API_BELOW_BASIC_PCT',
                                                           'MATH_API_BASIC_PCT', 
                                                           'MATH_API_PROFICIENT_PCT', 
                                                           'MATH_API_ADVANCED_PCT',
                                            'MATH_BLACK_BELOW_BASIC_PCT',
                                                           'MATH_BLACK_BASIC_PCT', 
                                                           'MATH_BLACK_PROFICIENT_PCT', 
                                                           'MATH_BLACK_ADVANCED_PCT',
                                            'MATH_HISP_BELOW_BASIC_PCT',
                                                           'MATH_HISP_BASIC_PCT', 
                                                           'MATH_HISP_PROFICIENT_PCT', 
                                                           'MATH_HISP_ADVANCED_PCT',
                                            'MATH_MULTI_BELOW_BASIC_PCT',
                                                           'MATH_MULTI_BASIC_PCT', 
                                                           'MATH_MULTI_PROFICIENT_PCT', 
                                                           'MATH_MULTI_ADVANCED_PCT',
                                            'MATH_NATIVE_BELOW_BASIC_PCT',
                                                           'MATH_NATIVE_BASIC_PCT', 
                                                           'MATH_NATIVE_PROFICIENT_PCT', 
                                                           'MATH_NATIVE_ADVANCED_PCT',
                                           'SCI_WHITE_BELOW_BASIC_PCT',
                                                           'SCI_WHITE_BASIC_PCT', 
                                                           'SCI_WHITE_PROFICIENT_PCT', 
                                                           'SCI_WHITE_ADVANCED_PCT',
                                            'SCI_API_BELOW_BASIC_PCT',
                                                           'SCI_API_BASIC_PCT', 
                                                           'SCI_API_PROFICIENT_PCT', 
                                                           'SCI_API_ADVANCED_PCT',
                                            'SCI_BLACK_BELOW_BASIC_PCT',
                                                           'SCI_BLACK_BASIC_PCT', 
                                                           'SCI_BLACK_PROFICIENT_PCT', 
                                                           'SCI_BLACK_ADVANCED_PCT',
                                            'SCI_HISP_BELOW_BASIC_PCT',
                                                           'SCI_HISP_BASIC_PCT', 
                                                           'SCI_HISP_PROFICIENT_PCT', 
                                                           'SCI_HISP_ADVANCED_PCT',
                                            'SCI_MULTI_BELOW_BASIC_PCT',
                                                           'SCI_MULTI_BASIC_PCT', 
                                                           'SCI_MULTI_PROFICIENT_PCT', 
                                                           'SCI_MULTI_ADVANCED_PCT',
                                            'SCI_NATIVE_BELOW_BASIC_PCT',
                                                           'SCI_NATIVE_BASIC_PCT', 
                                                           'SCI_NATIVE_PROFICIENT_PCT',
                                                           'SCI_NATIVE_ADVANCED_PCT']])

MAP_Scores_Index['ENG_BEL_INDEX'] = MAP_Scores_Index['ENG_WHITE_BELOW_BASIC_PCT']/MAP_Scores_Index[['ENG_API_BELOW_BASIC_PCT', 
                                                                                                    'ENG_BLACK_BELOW_BASIC_PCT', 
                                                                                                    'ENG_HISP_BELOW_BASIC_PCT',
                                                                                                   'ENG_MULTI_BELOW_BASIC_PCT',
                                                                                                   'ENG_NATIVE_BELOW_BASIC_PCT']].mean(axis=1)
MAP_Scores_Index['ENG_BAS_INDEX'] = MAP_Scores_Index['ENG_WHITE_BASIC_PCT']/MAP_Scores_Index[['ENG_API_BASIC_PCT', 
                                                                                                    'ENG_BLACK_BASIC_PCT', 
                                                                                                    'ENG_HISP_BASIC_PCT',
                                                                                                   'ENG_MULTI_BASIC_PCT',
                                                                                                   'ENG_NATIVE_BASIC_PCT']].mean(axis=1)
MAP_Scores_Index['ENG_PRO_INDEX'] = MAP_Scores_Index['ENG_WHITE_PROFICIENT_PCT']/MAP_Scores_Index[['ENG_API_PROFICIENT_PCT', 
                                                                                                    'ENG_BLACK_PROFICIENT_PCT', 
                                                                                                    'ENG_HISP_PROFICIENT_PCT',
                                                                                                   'ENG_MULTI_PROFICIENT_PCT',
                                                                                                   'ENG_NATIVE_PROFICIENT_PCT']].mean(axis=1)
MAP_Scores_Index['ENG_ADV_INDEX'] = MAP_Scores_Index['ENG_WHITE_ADVANCED_PCT']/MAP_Scores_Index[['ENG_API_ADVANCED_PCT', 
                                                                                                    'ENG_BLACK_ADVANCED_PCT', 
                                                                                                    'ENG_HISP_ADVANCED_PCT',
                                                                                                   'ENG_MULTI_ADVANCED_PCT',
                                                                                                   'ENG_NATIVE_ADVANCED_PCT']].mean(axis=1)

MAP_Scores_Index['MATH_BEL_INDEX'] = MAP_Scores_Index['MATH_WHITE_BELOW_BASIC_PCT']/MAP_Scores_Index[['MATH_API_BELOW_BASIC_PCT', 
                                                                                                    'MATH_BLACK_BELOW_BASIC_PCT', 
                                                                                                    'MATH_HISP_BELOW_BASIC_PCT',
                                                                                                   'MATH_MULTI_BELOW_BASIC_PCT',
                                                                                                   'MATH_NATIVE_BELOW_BASIC_PCT']].mean(axis=1)
MAP_Scores_Index['MATH_BAS_INDEX'] = MAP_Scores_Index['MATH_WHITE_BASIC_PCT']/MAP_Scores_Index[['MATH_API_BASIC_PCT', 
                                                                                                    'MATH_BLACK_BASIC_PCT', 
                                                                                                    'MATH_HISP_BASIC_PCT',
                                                                                                   'MATH_MULTI_BASIC_PCT',
                                                                                                   'MATH_NATIVE_BASIC_PCT']].mean(axis=1)
MAP_Scores_Index['MATH_PRO_INDEX'] = MAP_Scores_Index['MATH_WHITE_PROFICIENT_PCT']/MAP_Scores_Index[['MATH_API_PROFICIENT_PCT', 
                                                                                                    'MATH_BLACK_PROFICIENT_PCT', 
                                                                                                    'MATH_HISP_PROFICIENT_PCT',
                                                                                                   'MATH_MULTI_PROFICIENT_PCT',
                                                                                                   'MATH_NATIVE_PROFICIENT_PCT']].mean(axis=1)
MAP_Scores_Index['MATH_ADV_INDEX'] = MAP_Scores_Index['MATH_WHITE_ADVANCED_PCT']/MAP_Scores_Index[['MATH_API_ADVANCED_PCT', 
                                                                                                    'MATH_BLACK_ADVANCED_PCT', 
                                                                                                    'MATH_HISP_ADVANCED_PCT',
                                                                                                   'MATH_MULTI_ADVANCED_PCT',
                                                                                                   'MATH_NATIVE_ADVANCED_PCT']].mean(axis=1)

MAP_Scores_Index['SCI_BEL_INDEX'] = MAP_Scores_Index['SCI_WHITE_BELOW_BASIC_PCT']/MAP_Scores_Index[['SCI_API_BELOW_BASIC_PCT', 
                                                                                                    'SCI_BLACK_BELOW_BASIC_PCT', 
                                                                                                    'SCI_HISP_BELOW_BASIC_PCT',
                                                                                                   'SCI_MULTI_BELOW_BASIC_PCT',
                                                                                                   'SCI_NATIVE_BELOW_BASIC_PCT']].mean(axis=1)
MAP_Scores_Index['SCI_BAS_INDEX'] = MAP_Scores_Index['SCI_WHITE_BASIC_PCT']/MAP_Scores_Index[['SCI_API_BASIC_PCT', 
                                                                                                    'SCI_BLACK_BASIC_PCT', 
                                                                                                    'SCI_HISP_BASIC_PCT',
                                                                                                   'SCI_MULTI_BASIC_PCT',
                                                                                                   'SCI_NATIVE_BASIC_PCT']].mean(axis=1)
MAP_Scores_Index['SCI_PRO_INDEX'] = MAP_Scores_Index['SCI_WHITE_PROFICIENT_PCT']/MAP_Scores_Index[['SCI_API_PROFICIENT_PCT', 
                                                                                                    'SCI_BLACK_PROFICIENT_PCT', 
                                                                                                    'SCI_HISP_PROFICIENT_PCT',
                                                                                                   'SCI_MULTI_PROFICIENT_PCT',
                                                                                                   'SCI_NATIVE_PROFICIENT_PCT']].mean(axis=1)
MAP_Scores_Index['SCI_ADV_INDEX'] = MAP_Scores_Index['SCI_WHITE_ADVANCED_PCT']/MAP_Scores_Index[['SCI_API_ADVANCED_PCT', 
                                                                                                    'SCI_BLACK_ADVANCED_PCT', 
                                                                                                    'SCI_HISP_ADVANCED_PCT',
                                                                                                   'SCI_MULTI_ADVANCED_PCT',
                                                                                                   'SCI_NATIVE_ADVANCED_PCT']].mean(axis=1)

#Check that all numeric data is set to dtype float64
MAP_Scores_Index.info()


<class 'pandas.core.frame.DataFrame'>
Int64Index: 2067 entries, 0 to 2066
Data columns (total 88 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   COUNTY_DISTRICT              2067 non-null   int64  
 1   DISTRICT_NAME                2067 non-null   object 
 2   SCHOOL_CODE                  2067 non-null   int64  
 3   SCHOOL_NAME                  2067 non-null   object 
 4   ENG_WHITE_BELOW_BASIC_PCT    1849 non-null   float64
 5   ENG_WHITE_BASIC_PCT          1870 non-null   float64
 6   ENG_WHITE_PROFICIENT_PCT     1882 non-null   float64
 7   ENG_WHITE_ADVANCED_PCT       1855 non-null   float64
 8   ENG_API_BELOW_BASIC_PCT      205 non-null    float64
 9   ENG_API_BASIC_PCT            244 non-null    float64
 10  ENG_API_PROFICIENT_PCT       282 non-null    float64
 11  ENG_API_ADVANCED_PCT         272 non-null    float64
 12  ENG_BLACK_BELOW_BASIC_PCT    798 non-null    float64
 13  ENG_BLACK_BASIC_PC

In [11]:
#Retreive Teacher Data from MO DESE MCDS portal > Teachers > Faculty Information > "Building Faculty Information (2012-20)"

Teacher_Data = pd.DataFrame(pd.read_csv('Teacher Data.csv'))

#Retreive only 2019 data
Teacher_Data = Teacher_Data[Teacher_Data['YEAR']== 2019].dropna()

#Rename school identifiers to prepare for a later merge
Teacher_Data.rename(columns = {'COUNTY_DISTRICT_CODE': 'DIST_CODE', 'SCHOOL_CODE': 'SCHL_CODE'}, inplace=True)

#Retreive only vriables of interest
Teacher_Data = Teacher_Data[['DIST_CODE','SCHL_CODE','ADMINISTRATOR_FTE','ADMINISTRATOR_SALARY_AVERAGE','TEACHER_FTE','TEACHER_SALARY_AVG','TEACHER_SALARY_AVG_REG_TERM','TEACHER_AVERAGE_YEARS_EXP','TEACHER_MAST_DEGREE_PERCENT']]

#reate a single school identifier
Teacher_Data['id']= Teacher_Data['DIST_CODE']*Teacher_Data['SCHL_CODE']

Teacher_Data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3283 entries, 7 to 26074
Data columns (total 10 columns):
 #   Column                        Non-Null Count  Dtype  
---  ------                        --------------  -----  
 0   DIST_CODE                     3283 non-null   int64  
 1   SCHL_CODE                     3283 non-null   int64  
 2   ADMINISTRATOR_FTE             3283 non-null   float64
 3   ADMINISTRATOR_SALARY_AVERAGE  3283 non-null   int64  
 4   TEACHER_FTE                   3283 non-null   float64
 5   TEACHER_SALARY_AVG            3283 non-null   int64  
 6   TEACHER_SALARY_AVG_REG_TERM   3283 non-null   int64  
 7   TEACHER_AVERAGE_YEARS_EXP     3283 non-null   float64
 8   TEACHER_MAST_DEGREE_PERCENT   3283 non-null   float64
 9   id                            3283 non-null   int64  
dtypes: float64(4), int64(6)
memory usage: 282.1 KB


In [13]:
#Retreive Student Demographic Data from MO DESE MCDS portal > Students > Enrollment & Demographics > "Building Demographic Data 2006-20"

Demographic_Data = pd.DataFrame(pd.read_csv('Demographics.csv'))

#Retrieve only 2019 data
Demographic_Data = Demographic_Data[Demographic_Data['YEAR'] == 2019]

#Remove symbols to change variables to a numeric dtype
Demographic_Data.replace("\*", np.NaN, regex= True, inplace = True)

#Rename identifying variables for later erge
Demographic_Data.rename(columns = {'COUNTY_DISTRICT_CODE': 'DIST_CODE', 'SCHOOL_CODE': 'SCHL_CODE'}, inplace=True)

#Change variables to a numeric dtype
Enroll_White_Pct = Demographic_Data['ENROLLMENT_WHITE_PCT'].astype(float)
Demographic_Data['PCT_WHITE'] = Enroll_White_Pct

Free_Reduc_Lunch = Demographic_Data['LUNCH_COUNT_FREE_REDUCED_PCT'].astype(float)
Demographic_Data['PCT_LUNCH'] = Free_Reduc_Lunch

#Retrieve variables of interest
Demographic_Data = Demographic_Data[['DIST_CODE','SCHL_CODE','PCT_WHITE','PCT_LUNCH']]

#Create single identifier for each school
Demographic_Data['id']= Demographic_Data['DIST_CODE']*Demographic_Data['SCHL_CODE']

Demographic_Data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2715 entries, 13 to 40423
Data columns (total 5 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   DIST_CODE  2715 non-null   int64  
 1   SCHL_CODE  2715 non-null   int64  
 2   PCT_WHITE  2128 non-null   float64
 3   PCT_LUNCH  1788 non-null   float64
 4   id         2715 non-null   int64  
dtypes: float64(2), int64(3)
memory usage: 127.3 KB


In [14]:
#Retreieve School Spending Data from MO DESE MCDS > Districts, Charters, & Schools > School Finance Data > "Building Level Per Pupil Expenditures 2019"

Expend = pd.DataFrame(pd.read_csv('Building Level Per Pupil Expenditures 2019.csv'))

#Remove symbols to change variables to dtype(float)
Expend.replace("\-", '', regex= True, inplace = True)
Expend.replace("\$", '', regex= True, inplace = True)
Expend.replace("\,", '', regex= True, inplace = True)

#Convert variables to dtype(float)
State_Local_Total = Expend['State and Local Expenditures Building'].astype(float)
Expend['Local_State_Total'] = State_Local_Total
Per_Student = Expend['Expenditures Per September Membership'].astype(float)
Expend['Per_Student'] = Per_Student

#Convert indetifiers to dtype(int)
Dist_Code = Expend['District Code'].astype(int)
Expend['DIST_CODE'] = Dist_Code
School_Code = Expend['Building Number'].astype(int)
Expend['SCHL_CODE'] = School_Code

#Retrieve variables of inbterest
Expend = Expend[['Local_State_Total','Per_Student','DIST_CODE','SCHL_CODE']]

#Create unique indentifier for al schools
Expend['id']= Expend['DIST_CODE']*Expend['SCHL_CODE']
Expend.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2714 entries, 0 to 2713
Data columns (total 5 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   Local_State_Total  2714 non-null   float64
 1   Per_Student        2714 non-null   float64
 2   DIST_CODE          2714 non-null   int32  
 3   SCHL_CODE          2714 non-null   int32  
 4   id                 2714 non-null   int32  
dtypes: float64(2), int32(3)
memory usage: 74.3 KB


In [15]:
#Retreive school address data from this list hosted by MO DESE https://apps.dese.mo.gov/MCDS/Reports/SSRS_Print.aspx?ReportId=9cebc711-eb02-48bd-ae0e-47f11d8ef9f4

School_Info = pd.DataFrame(pd.read_csv('School Building List (1).csv'))

#Retreive variabes
School_Info = School_Info[['CTYDIST', 
                           'SCHNUM',
                          'SCHNAME',
                          'DNAME',
                          'SCHADDR1',
                          'SCHADDR2',
                          'SCHCITY',
                          'SCHZIP']]
School_Info.info()



<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2421 entries, 0 to 2420
Data columns (total 8 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   CTYDIST   2421 non-null   int64 
 1   SCHNUM    2421 non-null   int64 
 2   SCHNAME   2421 non-null   object
 3   DNAME     2421 non-null   object
 4   SCHADDR1  2421 non-null   object
 5   SCHADDR2  564 non-null    object
 6   SCHCITY   2421 non-null   object
 7   SCHZIP    2421 non-null   int64 
dtypes: int64(3), object(5)
memory usage: 151.4+ KB


2. Find geodata for each school

In [47]:
#Name useragent for geopy
locator = Nominatim(user_agent="MO_Schools")

from geopy.extra.rate_limiter import RateLimiter

#Name df
df = School_Info
df['ADDRESS'] = df['SCHADDR1'] + " " + df['SCHCITY'] + ", MO"

# 1 - conveneint function to delay between geocoding calls
geocode = RateLimiter(locator.geocode, min_delay_seconds=1)
# 2- - create location column
df['location'] = df['ADDRESS'].apply(geocode)
# 3 - create longitude, laatitude and altitude from location column (returns tuple)
df['point'] = df['location'].apply(lambda loc: tuple(loc.point) if loc else None)
# 4 - split point column into latitude, longitude and altitude columns
df[['latitude', 'longitude', 'altitude']] = pd.DataFrame(df['point'].tolist(), index=df.index)

RateLimiter caught an error, retrying (0/2 tries). Called with (*('201 S Washington  La Monte , MO',), **{}).
Traceback (most recent call last):
  File "C:\Users\johns\anaconda3\lib\site-packages\urllib3\connectionpool.py", line 426, in _make_request
    six.raise_from(e, None)
  File "<string>", line 3, in raise_from
  File "C:\Users\johns\anaconda3\lib\site-packages\urllib3\connectionpool.py", line 421, in _make_request
    httplib_response = conn.getresponse()
  File "C:\Users\johns\anaconda3\lib\http\client.py", line 1347, in getresponse
    response.begin()
  File "C:\Users\johns\anaconda3\lib\http\client.py", line 307, in begin
    version, status, reason = self._read_status()
  File "C:\Users\johns\anaconda3\lib\http\client.py", line 268, in _read_status
    line = str(self.fp.readline(_MAXLINE + 1), "iso-8859-1")
  File "C:\Users\johns\anaconda3\lib\socket.py", line 669, in readinto
    return self._sock.recv_into(b)
  File "C:\Users\johns\anaconda3\lib\ssl.py", line 1241, in r

In [18]:


#Rename df that now has geodata for school to School_Info
School_Loc = df[['CTYDIST', 'SCHNUM', 'SCHNAME', 'latitude', 'longitude']]

#Rename identifiers for merge later on
School_Loc.rename(columns={'CTYDIST': 'DIST_CODE', 'SCHNUM': 'SCHL_CODE'}, inplace=True)

#Create unique indentifier for each school
School_Loc['id'] = School_Loc['DIST_CODE']*School_Loc['SCHL_CODE']


KeyError: "['CTYDIST', 'SCHNUM'] not in index"

In [19]:
#Merge MAP data with school geo data
MAP_Scores_Index.rename(columns = {'COUNTY_DISTRICT': 'DIST_CODE', 'SCHOOL_CODE': 'SCHL_CODE'}, inplace=True)
MAP_Scores_Index.head()
School_Loc = pd.DataFrame(pd.read_csv('School Geo Data.csv')).dropna()
School_Loc['id'] = School_Loc['DIST_CODE']*School_Loc['SCHL_CODE']
Score_Loc = School_Loc.merge(MAP_Scores_Index)
Score_Loc['id']= Score_Loc['DIST_CODE']*Score_Loc['SCHL_CODE']

#Remove schools that were assigned geodata outside the state of Missouri, use folium map to check this
Score_Loc.drop(Score_Loc.loc[Score_Loc['id'] == 255144000].index, inplace=True)
Score_Loc.drop(Score_Loc.loc[Score_Loc['id'] == 92475600].index, inplace=True)
Score_Loc.drop(Score_Loc.loc[Score_Loc['id'] == 76938780].index, inplace=True)
Score_Loc.drop(Score_Loc.loc[Score_Loc['id'] == 97323600].index, inplace=True)
Score_Loc.drop(Score_Loc.loc[Score_Loc['id'] == 252015000].index, inplace=True)
Score_Loc.drop(Score_Loc.loc[Score_Loc['id'] == 30453150].index, inplace=True)
Score_Loc.drop(Score_Loc.loc[Score_Loc['id'] == 160058060].index, inplace=True)
Score_Loc.drop(Score_Loc.loc[Score_Loc['id'] == 354049440].index, inplace=True)
Score_Loc.drop(Score_Loc.loc[Score_Loc['id'] == 20095950].index, inplace=True)
Score_Loc.drop(Score_Loc.loc[Score_Loc['id'] == 88205250].index, inplace=True)
Score_Loc.drop(Score_Loc.loc[Score_Loc['id'] == 337700100].index, inplace=True)
School_Loc.head()

Unnamed: 0  DIST_CODE  SCHL_CODE                          SCHNAME  \
0           0     115933       6905                Atlas Elementary    
1           1      48914       1920   Academie Lafayette Armour Ihs    
2           2      48914       1910    Academie Lafayette Armour IMS   
3           3      48914       6941  Academie Lafayette Cherry Elem    
4           4      48914       6940      Academie Lafayette Oak Elem   

    latitude  longitude         id  
0  38.634399 -90.250249  800517365  
1  39.063350 -94.582768   93914880  
2  39.063350 -94.582768   93425740  
3  39.064472 -94.577864  339512074  
4  39.002659 -94.584264  339463160

In [48]:
#Use Floium to ensure all schools were assigned geo data within the state of Missouri

df = Score_Loc
map_schools = folium.Map(location=[38.57751, -92.17784],zoom_start=7, tiles = 'Stamen Toner')
for lat,lan,id in zip(df['latitude'].dropna(),df['longitude'].dropna(),df['id']):
    folium.CircleMarker(
    location=[lat, lan],
    radius= 3,
    color= 'green',
    fill=True,
    fill_color="green",
    popup = id).add_to(map_schools)
map_schools

3. Visualize racial disparities in student performance at each school

In [49]:
#Retrieve a df that includes school location data with "MATH_BEL_INDEX"
Math_Bel_Loc = Score_Loc[['SCHNAME', 'latitude', 'longitude', 'MATH_BEL_INDEX', 'id']].dropna()

#Create a label for each school's index

#1 represents a school with more non-white students performing Bellow Basic in Math than white students
#2 represents a school with a more 1:1 relationship between white students and non-white students performing BEllow Basic at Math
#3 represets a schools with more white student performing Bellow Basic in Math than nn-white students
results = []
for n in Math_Bel_Loc['MATH_BEL_INDEX']:
    if n <= .75:
        results.append(1)
    elif n <= 1.25:
        results.append(2)
    else:
        results.append(3)
Math_Bel_Loc['Concern'] = results

Math_Bel_Loc.info()


<class 'pandas.core.frame.DataFrame'>
Int64Index: 689 entries, 0 to 1331
Data columns (total 6 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   SCHNAME         689 non-null    object 
 1   latitude        689 non-null    float64
 2   longitude       689 non-null    float64
 3   MATH_BEL_INDEX  689 non-null    float64
 4   id              689 non-null    int64  
 5   Concern         689 non-null    int64  
dtypes: float64(3), int64(2), object(1)
memory usage: 37.7+ KB


In [51]:
#Map the index scores to visualize where non-white students tend to perform Bellow Basic more that white students
df = Math_Bel_Loc
map = folium.Map(location=[38.57751, -92.17784],zoom_start=7, tiles = 'Stamen Toner')
def color(index):
    if index == 1:
        col = 'red'
    elif index == 2:
        col = 'green'
    elif index == 3:
        col = 'orange'
    else:
        col='black'
    return col
for lat,lan,index,code in zip(df['latitude'],df['longitude'],df['Concern'],df['SCHNAME']):
    folium.CircleMarker(
    location=[lat, lan],
    radius= 3,
    color= color(index),
    fill=True,
    fill_color="green",
    popup = code).add_to(map)
map

In [52]:
#Retreive a df that includes school location data with "MATH_ADV_INDEX"
Math_Adv_Loc = Score_Loc[['SCHNAME', 'latitude', 'longitude', 'MATH_ADV_INDEX']].dropna()

#Create a label for each school's index

#1 represents a school with more non-white students performing Advance in Math than white students
#2 represents a school with a more 1:1 relationship between white students and non-white students performing Advance at Math
#3 represets a schools with more white student performing Advance in Math than nn-white students
results = []
for n in Math_Adv_Loc['MATH_ADV_INDEX']:
    if n <= .75:
        results.append(1)
    elif n <= 1.25:
        results.append(2)
    else:
        results.append(3)
Math_Adv_Loc['Concern'] = results

Math_Adv_Loc.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 623 entries, 0 to 1331
Data columns (total 5 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   SCHNAME         623 non-null    object 
 1   latitude        623 non-null    float64
 2   longitude       623 non-null    float64
 3   MATH_ADV_INDEX  623 non-null    float64
 4   Concern         623 non-null    int64  
dtypes: float64(3), int64(1), object(1)
memory usage: 29.2+ KB


In [53]:
#MAP the index scores to see where more white student perform Advance on Math than non-white students

df = Math_Adv_Loc
map = folium.Map(location=[38.57751, -92.17784],zoom_start=7, tiles = 'Stamen Toner')
def color(index):
    if index == 3:
        col = 'red'
    elif index == 2:
        col = 'green'
    elif index == 1:
        col = 'orange'
    else:
        col='black'
    return col
for lat,lan,index in zip(df['latitude'],df['longitude'],df['Concern']):
    folium.CircleMarker(
    location=[lat, lan],
    radius= 3,
    color= color(index),
    fill=True,
    fill_color="green",).add_to(map)
map

4. Retreive venue data around each school with Four Square

In [20]:
#Create a df of just School identifers and geo data
df =Score_Loc[['id','latitude','longitude', 'DIST_CODE', 'SCHL_CODE']].dropna()
df.head()

id   latitude  longitude  DIST_CODE  SCHL_CODE
0   93425740  39.063350 -94.582768      48914       1910
1  339512074  39.064472 -94.577864      48914       6941
2  339463160  39.002659 -94.584264      48914       6940
3  342244365  38.983940 -94.576448      48927       6995
4    4381800  40.235950 -92.704427       1090       4020

In [45]:
#Input Four Square developer information 

CLIENT_ID = '****' # your Foursquare ID
CLIENT_SECRET = '****' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: ****
CLIENT_SECRET:****


In [139]:
#Test the Four Square API with one school

school_latitude = df.loc[0, 'latitude'] # neighborhood latitude value
school_longitude = df.loc[0, 'longitude'] # neighborhood longitude value

school_name = df.loc[0, 'id'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(id, 
                                                               school_latitude, 
                                                               school_longitude))

Latitude and longitude values of 9532950 are 39.06335025, -94.58276831279105.


In [140]:
# Create Four Squre API url

LIMIT = 100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    '2VO2XIZR3IWYNPILAZMVZ5ZR1EIJFDHREBJD4IFV1S2WNUZ5', 
    'O2YLEHM3D4ELWVKADCCNRUTOUQJETHHM1YH1I1CLYCZRUGUJ', 
    VERSION, 
    school_latitude, 
    school_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=2VO2XIZR3IWYNPILAZMVZ5ZR1EIJFDHREBJD4IFV1S2WNUZ5&client_secret=O2YLEHM3D4ELWVKADCCNRUTOUQJETHHM1YH1I1CLYCZRUGUJ&v=20180605&ll=39.06335025,-94.58276831279105&radius=500&limit=100'

In [141]:
#Retrieve the Four Square results of test school
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '61142ca16637b50726490b14'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Kansas City',
  'headerFullLocation': 'Kansas City',
  'headerLocationGranularity': 'city',
  'totalResults': 25,
  'suggestedBounds': {'ne': {'lat': 39.0678502545, 'lng': -94.57698351736177},
   'sw': {'lat': 39.0588502455, 'lng': -94.58855310822032}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b1e1461f964a520481724e3',
       'name': "Pancho's Mexican Food",
       'location': {'address': '3540 Main St',
        'crossStreet': 'at W 36th St',
        'lat': 39.06247,
        'lng': -94.58603,
        'labeledLatLngs': [{'label': 'display',
          'lat': 39.062

In [142]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [143]:
#Retreive select information about each venue of the test school

venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

<ipython-input-143-561c05f0fdd1>:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  nearby_venues = json_normalize(venues) # flatten JSON


name            categories        lat        lng
0      Pancho's Mexican Food    Mexican Restaurant  39.062470 -94.586030
1        Mother Earth Coffee           Coffee Shop  39.063249 -94.581383
2  LaMar's Donuts and Coffee            Donut Shop  39.065943 -94.585273
3                     Costco       Warehouse Store  39.067264 -94.581234
4                      Awaze  Ethiopian Restaurant  39.065220 -94.585477

In [144]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

25 venues were returned by Foursquare.


In [156]:
#Define a function to itterate this process for all schools

def getNearbyVenues(id, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for id, lat, lng in zip(id, latitudes, longitudes):
        print(id)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            '2VO2XIZR3IWYNPILAZMVZ5ZR1EIJFDHREBJD4IFV1S2WNUZ5', 
    'O2YLEHM3D4ELWVKADCCNRUTOUQJETHHM1YH1I1CLYCZRUGUJ', 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()['response']['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            id, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['id', 
                  'School Latitude', 
                  'School Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [157]:
# Use function to retreive venues data for all schools
school_venues = getNearbyVenues(id=df['id'],
                                   latitudes=df['latitude'],
                                   longitudes=df['longitude']
                                  )

93425740
339512074
339463160
342244365
4381800
1144500
414578580
108285450
100902900
288294000
39948300
114138000
338205735
96839820
192212370
317893560
301849740
78841350
189189240
141186000
157322700
41091750
245823000
64207500
57865500
223746600
137178480
35830200
102372000
197522700
309946020
80956050
28630440
7478100
386317980
192198000
100903950
414574560
108284400
20109600
77757120
77374080
78331680
78140160
414602700
108291750
245827020
64208550
378185520
98779800
108761100
414586620
108287550
309393000
109247250
148530120
243704760
88201050
339364040
252003000
28414050
109326440
81183000
17980200
330042000
86205000
246300000
333326000
111304200
217308200
431436280
429316200
428256160
432496320
52505220
13714050
52477080
13706700
100906050
288303000
388248040
339966200
193218200
85018980
22206450
11632950
28658580
7485450
430763100
112512750
321465000
169310340
44222850
245851140
15752100
45006000
60758100
60608080
60458060
61208160
26251050
101004040
75003000
64705920
65188800

In [264]:
#Save results to a csv file to prevent makig additional calls to the API
school_venues.to_csv(r'School Venues')
print("SAVED!")

SAVED!


In [4]:
school_venues = pd.DataFrame(pd.read_csv('School Venues'))
print(school_venues.shape)
school_venues.head()

(6138, 8)


Unnamed: 0        id  School Latitude  School Longitude  \
0           0  93425740         39.06335        -94.582768   
1           1  93425740         39.06335        -94.582768   
2           2  93425740         39.06335        -94.582768   
3           3  93425740         39.06335        -94.582768   
4           4  93425740         39.06335        -94.582768   

                       Venue  Venue Latitude  Venue Longitude  \
0      Pancho's Mexican Food       39.062470       -94.586030   
1        Mother Earth Coffee       39.063249       -94.581383   
2  LaMar's Donuts and Coffee       39.065943       -94.585273   
3                     Costco       39.067264       -94.581234   
4                      Awaze       39.065220       -94.585477   

         Venue Category  
0    Mexican Restaurant  
1           Coffee Shop  
2            Donut Shop  
3       Warehouse Store  
4  Ethiopian Restaurant

In [7]:
#Group all venues by school
school_venues.groupby('id').count()

Unnamed: 0  School Latitude  School Longitude  Venue  \
id                                                                 
1144500              1                1                 1      1   
2201850              8                8                 8      8   
3183600              4                4                 4      4   
3184650              2                2                 2      2   
4315500              4                4                 4      4   
4381800              1                1                 1      1   
4418550              1                1                 1      1   
5378100              2                2                 2      2   
5379150              4                4                 4      4   
5384400              2                2                 2      2   
6291000              8                8                 8      8   
7485450              1                1                 1      1   
10294860             9                9                 9      9   
10594500             3                3                 3      3   
10595550             5                5                 5      5   
10597650            13               13                13     13   
10698580             2                2                 2      2   
10849975             5                5                 5      5   
11629800             5                5                 5      5   
11632950             1                1                 1      1   
11913150             4                4                 4      4   
12184620             2                2                 2      2   
12188640             4                4                 4      4   
12192660             2                2                 2      2   
12713400             1                1                 1      1   
13707750             4                4                 4      4   
13711950             4                4                 4      4   
13714050             2                2                 2      2   
14832300             2                2                 2      2   
14833350             2                2                 2      2   
14835450             7                7                 7      7   
15369000             4                4                 4      4   
15752100             8                8                 8      8   
16768800             1                1                 1      1   
16894500            11               11                11     11   
16900800             3                3                 3      3   
17977050             2                2                 2      2   
17980200             2                2                 2      2   
18949350             2                2                 2      2   
20099100             4                4                 4      4   
20105400             3                3                 3      3   
20109600             3                3                 3      3   
20512000             5                5                 5      5   
20590440             2                2                 2      2   
20610540             3                3                 3      3   
20645690             4                4                 4      4   
20690650             6                6                 6      6   
20717120             6                6                 6      6   
20791580             5                5                 5      5   
20942975             6                6                 6      6   
21002100             2                2                 2      2   
22206450             2                2                 2      2   
22208550             1                1                 1      1   
23193450             3                3                 3      3   
23198700             2                2                 2      2   
24526020             1                1                 1      1   
24571800            49               49                49     49   


In [8]:
print('There are {} uniques categories.'.format(len(school_venues['Venue Category'].unique())))

There are 358 uniques categories.


In [5]:
#Prepare Venue data for kMeans analysis using onehot encoding

# one hot encoding
school_onehot = pd.get_dummies(school_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
school_onehot['id'] = school_venues['id'] 

# move neighborhood column to the first column
fixed_columns = [school_onehot.columns[-1]] + list(school_onehot.columns[:-1])
school_onehot = school_onehot[fixed_columns]

school_onehot.head()

id  ATM  Accessories Store  American Restaurant  Antique Shop  \
0  93425740    0                  0                    0             0   
1  93425740    0                  0                    0             0   
2  93425740    0                  0                    0             0   
3  93425740    0                  0                    0             0   
4  93425740    0                  0                    0             0   

   Aquarium  Arcade  Art Gallery  Art Museum  Arts & Crafts Store  \
0         0       0            0           0                    0   
1         0       0            0           0                    0   
2         0       0            0           0                    0   
3         0       0            0           0                    0   
4         0       0            0           0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                     0                 0                   0            0   
1                     0                 0                   0            0   
2                     0                 0                   0            0   
3                     0                 0                   0            0   
4                     0                 0                   0            0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0              0                0          0           0           0       0   
1              0                0          0           0           0       0   
2              0                0          0           0           0       0   
3              0                0          0           0           0       0   
4              0                0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0     0    0               0                 0                 0   
1     0    0               0                 0                 0   
2     0    0               0                 0                 0   
3     0    0               0                 0                 0   
4     0    0               0                 0                 0   

   Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  Beer Garden  \
0                   0      0                0         0            0   
1                   0      0                0         0            0   
2                   0      0                0         0            0   
3                   0      0                0         0            0   
4                   0      0                0         0            0   

   Beer Store  Big Box Store  Bike Shop  Bistro  Board Shop  Boat or Ferry  \
0           0              0          0       0           0              0   
1           0              0          0       0           0              0   
2           0              0          0       0           0              0   
3           0              0          0       0           0              0   
4           0              0          0       0           0              0   

   Bookstore  Bosnian Restaurant  Botanical Garden  Boutique  Bowling Alley  \
0          0                   0                 0         0              0   
1          0                   0                 0         0              0   
2          0                   0                 0         0              0   
3          0                   0                 0         0              0   
4          0                   0                 0         0              0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Bu

In [6]:
school_onehot.shape

(6138, 359)

In [7]:
#Find the avg occurence of all venue categories for each school

school_grouped = school_onehot.groupby('id').mean().reset_index()
school_grouped.head()

id  ATM  Accessories Store  American Restaurant  Antique Shop  \
0  1144500  0.0                0.0                  0.0           0.0   
1  2201850  0.0                0.0                  0.0           0.0   
2  3183600  0.0                0.0                  0.0           0.0   
3  3184650  0.0                0.0                  0.0           0.0   
4  4315500  0.0                0.0                  0.0           0.0   

   Aquarium  Arcade  Art Gallery  Art Museum  Arts & Crafts Store  \
0       0.0     0.0          0.0         0.0                  0.0   
1       0.0     0.0          0.0         0.0                  0.0   
2       0.0     0.0          0.0         0.0                  0.0   
3       0.0     0.0          0.0         0.0                  0.0   
4       0.0     0.0          0.0         0.0                  0.0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                   0.0               0.0                 0.0          0.0   
1                   0.0               0.0                 0.0          0.0   
2                   0.0               0.0                 0.0          0.0   
3                   0.0               0.0                 0.0          0.0   
4                   0.0               0.0                 0.0          0.0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0            0.0              0.0        0.0         0.0         0.0     0.0   
1            0.0              0.0        0.0         0.0         0.0     0.0   
2            0.0              0.0        0.0         0.0         0.0     0.0   
3            0.0              0.0        0.0         0.0         0.0     0.0   
4            0.0              0.0        0.0         0.0         0.0     0.0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  \
0   0.0  0.0             0.0               0.0               0.0   
1   0.0  0.0             0.0               0.0               0.0   
2   0.0  0.0             0.0               0.0               0.0   
3   0.0  0.0             0.0               0.0               0.0   
4   0.0  0.0             0.0               0.0               0.0   

   Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  Beer Garden  \
0                 0.0    0.0              0.0       0.0          0.0   
1                 0.0    0.0              0.0       0.0          0.0   
2                 0.0    0.0              0.0       0.0          0.0   
3                 0.0    0.0              0.0       0.0          0.0   
4                 0.0    0.0              0.0       0.0          0.0   

   Beer Store  Big Box Store  Bike Shop  Bistro  Board Shop  Boat or Ferry  \
0         0.0            0.0        0.0     0.0         0.0            0.0   
1         0.0            0.0        0.0     0.0         0.0            0.0   
2         0.0            0.0        0.0     0.0         0.0            0.0   
3         0.0            0.0        0.0     0.0         0.0            0.0   
4         0.0            0.0        0.0     0.0         0.0            0.0   

   Bookstore  Bosnian Restaurant  Botanical Garden  Boutique  Bowling Alley  \
0        0.0                 0.0               0.0       0.0           0.00   
1        0.0                 0.0               0.0       0.0           0.00   
2        0.0                 0.0               0.0       0.0           0.25   
3        0.0                 0.0               0.0       0.0           0.00   
4        0.0                 0.0               0.0       0.0           0.00   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                   0.0             0.0      0.0          0.0   
1                   0.0             0.0      0.0          0.0   
2                   0.0             0.0      0.0          0.0   
3                   0.0             0.0      0.0          0.0   
4                   0.0             0.0      0.0          0.0   

   Bubble Tea Shop  Buffet 

In [8]:
#Define a function to analyze top venues for each school
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [9]:
#Use the function to analyze top venues for each school
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['id']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
schools_venues_sorted = pd.DataFrame(columns=columns)
schools_venues_sorted['id'] = school_grouped['id']

for ind in np.arange(school_grouped.shape[0]):
    schools_venues_sorted.iloc[ind, 1:] = return_most_common_venues(school_grouped.iloc[ind, :], num_top_venues)

schools_venues_sorted.head()

id 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0  1144500     Convenience Store           Zoo Exhibit                 Field   
1  2201850           Video Store                  Food         Grocery Store   
2  3183600           Post Office              Pharmacy         Bowling Alley   
3  3184650           Post Office                 Diner                 Field   
4  4315500  Fast Food Restaurant           Pizza Place           Zoo Exhibit   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0         Event Service           Event Space            Eye Doctor   
1        Sandwich Place           Gas Station                  Café   
2     Health Food Store         Event Service           Event Space   
3         Event Service           Event Space            Eye Doctor   
4         Event Service           Event Space            Eye Doctor   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0           Fabric Shop               Factory    Falafel Restaurant   
1        Discount Store  Fast Food Restaurant                  Farm   
2            Eye Doctor           Fabric Shop               Factory   
3           Fabric Shop               Factory    Falafel Restaurant   
4           Fabric Shop               Factory    Falafel Restaurant   

  10th Most Common Venue  
0                   Farm  
1            Event Space  
2     Falafel Restaurant  
3                   Farm  
4                   Farm

5. Cluster schools using KMeans clustering

In [20]:
#Retreive a df of just Math and English performance disparity data
Score_Loc = Score_Loc[['id',
                       'MATH_BEL_INDEX',
                       'MATH_BAS_INDEX',
                      'MATH_PRO_INDEX',
                      'MATH_ADV_INDEX',
                      'ENG_BEL_INDEX',
                       'ENG_BAS_INDEX',
                      'ENG_PRO_INDEX',
                      'ENG_ADV_INDEX']]
Score_Loc.head()

id  MATH_BEL_INDEX  MATH_BAS_INDEX  MATH_PRO_INDEX  MATH_ADV_INDEX  \
0   93425740        0.156977        0.728448        0.897463        1.617769   
1  339512074        0.124711        0.289544        1.842294        2.235294   
2  339463160        0.297203        0.728614        1.064748        1.680180   
3  342244365             NaN             NaN             NaN             NaN   
4    4381800             NaN             NaN             NaN             NaN   

   ENG_BEL_INDEX  ENG_BAS_INDEX  ENG_PRO_INDEX  ENG_ADV_INDEX  
0       0.053763       0.249046       1.000000       1.455000  
1       0.237347       0.759076       1.068607       2.608187  
2       0.348754       0.505604       1.131313       2.565217  
3            NaN            NaN            NaN            NaN  
4            NaN            NaN            NaN            NaN

In [21]:
#Merge all data to one df for clustering.
#Ensure identfiers and dtype(ogj) variables are removed
venue_data = school_grouped
merge1 = pd.DataFrame(pd.merge(venue_data, Score_Loc))
merge2 = pd.DataFrame(pd.merge(merge1, Teacher_Data))
merge3 = pd.DataFrame(pd.merge(merge2, Demographic_Data))
All_Data = pd.DataFrame(pd.merge(merge3, Expend)).dropna()
All_Data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 411 entries, 4 to 1129
Columns: 380 entries, id to Per_Student
dtypes: float64(374), int64(6)
memory usage: 1.2 MB


In [22]:
# set number of clusters
kclusters = 7

school_grouped_clustering = All_Data.drop('id', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(school_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0])

In [23]:
# add clustering labels to df
All_Data.insert(0, 'Cluster Labels', kmeans.labels_)



6. Visualize cluster labels and review cluster label profiles

In [24]:
All_Data_Loc = pd.DataFrame(pd.merge(All_Data, School_Loc, on = 'id'))
All_Data_Loc.head()

Cluster Labels        id  ATM  Accessories Store  American Restaurant  \
0               0   4315500  0.0                0.0                  0.0   
1               0   4418550  0.0                0.0                  0.0   
2               0   5384400  0.0                0.0                  0.0   
3               0   6291000  0.0                0.0                  0.0   
4               0  10597650  0.0                0.0                  0.0   

   Antique Shop  Aquarium  Arcade  Art Gallery  Art Museum  \
0           0.0       0.0     0.0          0.0         0.0   
1           0.0       0.0     0.0          0.0         0.0   
2           0.0       0.0     0.0          0.0         0.0   
3           0.0       0.0     0.0          0.0         0.0   
4           0.0       0.0     0.0          0.0         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                  0.0                   0.0               0.0   
1                  0.0                   0.0               0.0   
2                  0.0                   0.0               0.0   
3                  0.0                   0.0               0.0   
4                  0.0                   0.0               0.0   

   Athletics & Sports  Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  \
0                 0.0          0.0            0.0              0.0        0.0   
1                 0.0          0.0            0.0              0.0        0.0   
2                 0.0          0.0            0.0              0.0        0.0   
3                 0.0          0.0            0.0              0.0        0.0   
4                 0.0          0.0            0.0              0.0        0.0   

   Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0         0.0         0.0     0.0   0.0  0.0             0.0   
1         0.0         0.0     0.0   0.0  0.0             0.0   
2         0.0         0.0     0.0   0.0  0.0             0.0   
3         0.0         0.0     0.0   0.0  0.0             0.0   
4         0.0         0.0     0.0   0.0  0.0             0.0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Beach  \
0               0.0               0.0                 0.0    0.0   
1               0.0               0.0                 0.0    0.0   
2               0.0               0.0                 0.0    0.0   
3               0.0               0.0                 0.0    0.0   
4               0.0               0.0                 0.0    0.0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0              0.0       0.0          0.0         0.0            0.0   
1              0.0       0.0          0.0         0.0            0.0   
2              0.0       0.0          0.0         0.0            0.0   
3              0.0       0.0          0.0         0.0            0.0   
4              0.0       0.0          0.0         0.0            0.0   

   Bike Shop  Bistro  Board Shop  Boat or Ferry  Bookstore  \
0        0.0     0.0         0.0            0.0        0.0   
1        0.0     0.0         0.0            0.0        0.0   
2        0.0     0.0         0.0            0.0        0.0   
3        0.0     0.0         0.0            0.0        0.0   
4        0.0     0.0         0.0            0.0        0.0   

   Bosnian Restaurant  Botanical Garden  Boutique  Bowling Alley  \
0                 0.0               0.0       0.0            0.0   
1                 0.0               0.0       0.0            0.0   
2                 0.0               0.0       0.0            0.0   
3                 0.0               0.0       0.0            0.0   
4                 0.0               0.0       0.0            0.0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                   0.0             0.0      0.0          0.0   
1                   0.0             0.0      0.0          0.0   
2                   0.0             0.0      0.0          0.0   
3                   

In [25]:
# create map
map_clusters = folium.Map(location=[38.57751, -92.17784],zoom_start=7, tiles = 'Stamen Toner')

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(All_Data_Loc['latitude'], All_Data_Loc['longitude'], All_Data_Loc['SCHNAME'], All_Data_Loc['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [32]:
#Drop all data other than venue data for cluster venue analysis
All_Data_Loc.drop(columns=['MATH_BEL_INDEX','MATH_BAS_INDEX','MATH_PRO_INDEX','MATH_ADV_INDEX','ENG_BEL_INDEX','ENG_BAS_INDEX','ENG_PRO_INDEX','ENG_ADV_INDEX','DIST_CODE_x','SCHL_CODE_x','ADMINISTRATOR_FTE','ADMINISTRATOR_SALARY_AVERAGE','TEACHER_FTE','TEACHER_SALARY_AVG','TEACHER_SALARY_AVG_REG_TERM','TEACHER_AVERAGE_YEARS_EXP','TEACHER_MAST_DEGREE_PERCENT','PCT_WHITE','PCT_LUNCH','Local_State_Total','Per_Student','Unnamed: 0','DIST_CODE_y','SCHL_CODE_y','SCHNAME','latitude','longitude'], inplace=True)


In [33]:
#Create a df with just venue data for each of the seven clusters
Cluster_Venues = All_Data_Loc.groupby(['Cluster Labels']).mean().reset_index().drop(columns = ['id','Cluster Labels'])
trans = Cluster_Venues.transpose()
cols = trans.columns.values.tolist()

#Create a list report of the top ten venues of each cluster
for col in cols:
    print('-----------------------------------')
    print("top venues in cluster ", col, "are ")
    print('-----------------------------------')
    print(trans.nlargest(10, col)[col])

-----------------------------------
top venues in cluster  0 are 
-----------------------------------
Pool                          0.050037
Gym / Fitness Center          0.049695
Park                          0.031273
Pizza Place                   0.030452
Construction & Landscaping    0.029494
Trail                         0.028090
Furniture / Home Store        0.024515
Playground                    0.024145
Athletics & Sports            0.021910
American Restaurant           0.020330
Name: 0, dtype: float64
-----------------------------------
top venues in cluster  1 are 
-----------------------------------
Park                          0.070418
Pizza Place                   0.051086
Playground                    0.043290
Construction & Landscaping    0.042208
Home Service                  0.035065
Gym / Fitness Center          0.029994
Gym                           0.028055
American Restaurant           0.025819
Athletics & Sports            0.024784
Fast Food Restaurant          0

In [36]:
#Create a df of cluster data without venue data.
#Be sure to redefine All_Data_Loc to access the cols that were previously dropped
Cluster_Data = All_Data_Loc[['Cluster Labels','MATH_BEL_INDEX','MATH_BAS_INDEX','MATH_PRO_INDEX','MATH_ADV_INDEX','ENG_BEL_INDEX','ENG_BAS_INDEX','ENG_PRO_INDEX','ENG_ADV_INDEX','ADMINISTRATOR_FTE','ADMINISTRATOR_SALARY_AVERAGE','TEACHER_FTE','TEACHER_SALARY_AVG','TEACHER_SALARY_AVG_REG_TERM','TEACHER_AVERAGE_YEARS_EXP','TEACHER_MAST_DEGREE_PERCENT','PCT_WHITE','PCT_LUNCH','Local_State_Total','Per_Student']]
Cluster_Data = Cluster_Data.groupby('Cluster Labels').mean()

#Create an avg of Bello Basic and Basic indeces for each cluster label
Cluster_Data['Avg Under Performance Indeces'] = Cluster_Data[['MATH_BEL_INDEX','MATH_BAS_INDEX','ENG_BEL_INDEX','ENG_BAS_INDEX']].mean(axis=1)

#Create an avg of Proficient and Advance indeces for each cluster label
Cluster_Data['Avg Over Performance Indeces'] = Cluster_Data[['MATH_PRO_INDEX','MATH_ADV_INDEX','ENG_PRO_INDEX','ENG_ADV_INDEX']].mean(axis=1)

Cluster_Data.sort_values(by ='Avg Under Performance Indeces' )

MATH_BEL_INDEX  MATH_BAS_INDEX  MATH_PRO_INDEX  \
Cluster Labels                                                   
5                     0.453679        0.877391        1.303139   
0                     0.603953        0.976145        1.265727   
3                     0.623257        0.986565        1.404574   
1                     0.657864        0.976129        1.357067   
4                     0.700500        0.991461        1.491159   
2                     0.808693        1.015877        1.408311   
6                     1.279228        1.758976        1.050114   

                MATH_ADV_INDEX  ENG_BEL_INDEX  ENG_BAS_INDEX  ENG_PRO_INDEX  \
Cluster Labels                                                                
5                     1.610465       0.462014       0.690649       1.209476   
0                     1.459344       0.501454       0.836918       1.103185   
3                     1.820152       0.598039       0.923036       1.241331   
1                     1.437825       0.613343       0.894186       1.251857   
4                     1.630928       0.650863       0.817896       1.323906   
2                     1.811768       0.765774       0.861766       1.288614   
6                     0.880063       1.185426       1.200909       1.250106   

                ENG_ADV_INDEX  ADMINISTRATOR_FTE  \
Cluster Labels                                     
5                    1.838972           2.716471   
0                    1.560640           2.345955   
3                    1.826351           2.271622   
1                    1.630523           2.344805   
4                    1.805971           1.985185   
2                    1.842012           1.843810   
6                    1.216308           0.000000   

                ADMINISTRATOR_SALARY_AVERAGE  TEACHER_FTE  TEACHER_SALARY_AVG  \
Cluster Labels                                                                  
5                              120753.794118    52.107941        67583.691176   
0                              102287.775281    46.657753        59296.393258   
3                               81212.675676    40.350811        45994.972973   
1                               87799.363636    46.780000        51552.623377   
4                              103284.185185    40.223519        54651.203704   
2                               80229.095238    33.851310        46130.571429   
6                                   0.000000    29.200000        45678.500000   

                TEACHER_SALARY_AVG_REG_TERM  TEACHER_AVERAGE_YEARS_EXP  \
Cluster Labels                                                           
5                              66825.338235                  14.832353   
0                              58526.741573                  12.840449   
3                              44679.864865                  11.021622   
1                              49932.623377                  12.961039   
4                              53552.833333                  12.775926   
2                              45188.964286                  11.526190   
6                              45186.000000                  10.300000   

                TEACHER_MAST_DEGREE_PERCENT  PCT_WHITE  PCT_LUNCH  \
Cluster Labels                                                      
5                                 82.216176  62.165735  24.532353   
0                                 74.285393  69.419101  27.485393   
3                                 46.737838  73.204324  54.383784   
1                                 63.227273  74.708831  40.467532   
4                                 64.079630  59.668333  56.542593   
2                                 51.391667  70.941310  57.890476   
6                                 47.450000  64.565000  63.450000   

                Local_State_Total   Per_Student  \
Cluster Labels                                    
5                     9392.153088  12537.853676   
0                     8096.819775  10883.558315   
3                

In [37]:
#Create a df that shows who each cluster lael relates on other variables
Cluster_Profiles = Cluster_Data[['Avg Under Performance Indeces','Avg Over Performance Indeces','Per_Student','Local_State_Total','PCT_WHITE','PCT_LUNCH','TEACHER_AVERAGE_YEARS_EXP','TEACHER_MAST_DEGREE_PERCENT','TEACHER_SALARY_AVG','ADMINISTRATOR_SALARY_AVERAGE']]
#Create a descriptive label for each variable
Cluster_Profiles.rename(columns ={'Per_Student': 'Avg expenditures per student',
                                  'Local_State_Total': 'Avg total expenditures from state and local tax revenue',
                                  'PCT_WHITE': 'Avg % of student white',
                                  'PCT_LUNCH': 'Avg % of student with free or reduced lunch',
                                  'TEACHER_AVERAGE_YEARS_EXP': "Avg years experience of teachers",
                                  'TEACHER_MAST_DEGREE_PERCENT': 'Avg % of teachers with masters degrees',
                                  'TEACHER_SALARY_AVG':'Avg teacher salary',
                                  'ADMINISTRATOR_SALARY_AVERAGE':'Avg administrator salary'}, inplace = True )
Cluster_Profiles.sort_values(by = 'Avg Under Performance Indeces')

G:\anaconda3\lib\site-packages\pandas\core\frame.py:4441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().rename(


Avg Under Performance Indeces  Avg Over Performance Indeces  \
Cluster Labels                                                                
5                                    0.620933                      1.490513   
0                                    0.729617                      1.347224   
3                                    0.782724                      1.573102   
1                                    0.785381                      1.419318   
4                                    0.790180                      1.562991   
2                                    0.863027                      1.587676   
6                                    1.356135                      1.099148   

                Avg expenditures per student  \
Cluster Labels                                 
5                               12537.853676   
0                               10883.558315   
3                                9481.501351   
1                               10110.147532   
4                               10623.160741   
2                                9309.609286   
6                                9822.010000   

                Avg total expenditures from state and local tax revenue  \
Cluster Labels                                                            
5                                                     9392.153088         
0                                                     8096.819775         
3                                                     6421.489730         
1                                                     7117.881948         
4                                                     7223.825556         
2                                                     6168.009524         
6                                                     6260.950000         

                Avg % of student white  \
Cluster Labels                           
5                            62.165735   
0                            69.419101   
3                            73.204324   
1                            74.708831   
4                            59.668333   
2                            70.941310   
6                            64.565000   

                Avg % of student with free or reduced lunch  \
Cluster Labels                                                
5                                                 24.532353   
0                                                 27.485393   
3                                                 54.383784   
1                                                 40.467532   
4                                                 56.542593   
2                                                 57.890476   
6                                                 63.450000   

                Avg years experience of teachers  \
Cluster Labels                                     
5                                      14.832353   
0                                      12.840449   
3                                      11.021622   
1                                      12.961039   
4                                      12.775926   
2                                      11.526190   
6                                      10.300000   

                Avg % of teachers with masters degrees  Avg teacher salary  \
Cluster Labels                                                               
5                                            82.216176        67583.691176   
0                                            74.285393        59296.393258   
3                                            46.737838        45994.972973   
1                                            63.227273        51552.623377   
4                                            64.079630        54651.203704   
2                                            51.391667        46130.571429   
6                                            47.450000        45678.500000   

                Avg administrator salary  
Cluster Labels                   